In [1]:
from pylab import plt
import pandas as pd
import numpy as np
import sympy as sy
import matplotlib.pyplot as plt
import datetime as dt
import scipy as sc
from pylab import mpl
import scipy.integrate as sci
import scipy.stats as scs
import pandas_datareader as web
import statsmodels.api as sm
import enum
import scipy.optimize as spo
from numpy.fft import *
from yahoo_fin import options
from dawp import *
from mystic.solvers import fmin, fmin_powell, diffev, diffev2, sparsity,lattice

import datetime as dt
import numpy as np
import simpleplotly as spt
from fftoptionlib import *
import plotly
import plotly.offline as py
from scipy.stats import norm
import pandas as pd


import math
import sys
import yfinance as yf
np.set_printoptions(suppress=True, formatter={'all': lambda x: '%5.4f' % x})
aapl = yf.Ticker("NFLX")
sys.path.append('../')
sys.path.append('C:/Users/kiedy/dx')
print(sys.path)

import autograd.numpy as agnp
from autograd import grad


['C:\\Users\\kiedy', 'C:\\Users\\kiedy\\anaconda3\\python38.zip', 'C:\\Users\\kiedy\\anaconda3\\DLLs', 'C:\\Users\\kiedy\\anaconda3\\lib', 'C:\\Users\\kiedy\\anaconda3', '', 'C:\\Users\\kiedy\\anaconda3\\lib\\site-packages', 'C:\\Users\\kiedy\\anaconda3\\lib\\site-packages\\win32', 'C:\\Users\\kiedy\\anaconda3\\lib\\site-packages\\win32\\lib', 'C:\\Users\\kiedy\\anaconda3\\lib\\site-packages\\Pythonwin', 'C:\\Users\\kiedy\\anaconda3\\lib\\site-packages\\IPython\\extensions', 'C:\\Users\\kiedy\\.ipython', '../', 'C:/Users/kiedy/dx']


In [2]:
options1=pd.DataFrame([43.10, 35.60, 22.90, 20.20, 13.30],
                     columns=['price'])
options1['strike']=(1090,1100,1120,1125,1140)
options1['maturity']=dt.datetime(2002,5,17)
options1['T_2']=0.088


options2=pd.DataFrame([84.50, 64.30, 39.50, 33.50, 30.70, 28.00,  25.60, 23.20,19.10,15.30,12.10,10.90],
                     columns=['price'])
options2['strike']=(1050,1075,1110,1120,1125,1130,1135,1140,1150,1160,1170,1175)
options2['maturity']=dt.datetime(2002,6,21)
options2['T_2']=0.184


options3=pd.DataFrame([161.60, 144.80, 120.10, 100.70, 82.50,65.50,51.00,45.50,38.10,27.70,19.60,13.20],
                     columns=['price'])
options3['strike']=(975,995,1025,1050,1075,1100,1125,1135,1150,1175,1200,1225)
options3['maturity']=dt.datetime(2002,9,20)
options3['T_2']=0.436



options4=pd.DataFrame([173.30,157.00,133.10,114.80,97.60,81.20,66.90,58.90,53.90,42.50,33.00,24.90,18.30,13.20],
                     columns=['price'])
options4['strike']=(975,995,1025,1050,1075,1100,1125,1140,1150,1175,1200,1225,1250,1275)
options4['maturity']=dt.datetime(2002,12,20)
options4['T_2']=0.692


options5=pd.DataFrame([146.50,96.20,81.70,68.30,56.60,46.10,36.90,29.30,22.50,17.20,12.80],
                     columns=['price'])
options5['strike']=(1025,1100,1125,1150,1175,1200,1225,1250,1275,1300,1325)
options5['maturity']=dt.datetime(2003,3,21)
options5['T_2']=0.936


options6=pd.DataFrame([182.10,143.00,111.30,97.00,83.30,60.90,49.80,41.20,27.10,17.10,10.10],
                     columns=['price'])
options6['strike']=(995,1050,1100,1125,1150,1200,1225,1250,1300,1350,1400)
options6['maturity']=dt.datetime(2003,6,20)
options6['T_2']=1.192

options7=pd.DataFrame([171.40,140.40,112.80,99.80,66.90,49.50,35.70,25.20,17.00,12.20],
                     columns=['price'])
options7['strike']=(1050,1100,1150,1175,1250,1300,1350,1400,1450,1500)
options7['maturity']=dt.datetime(2003,12,19)
options7['T_2']=1.708

frames=[options1, options2, options3, options4, options5, options6, options7]

options=pd.concat(frames, ignore_index=True)
options['pricing_date'] = dt.datetime(2002, 4, 18)
options['T']=(options['maturity']-options['pricing_date']).dt.days/365.
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)


r=0.019
q=0.012
S0=1124.47
i = np.complex(0.0, 1.0)

T=1
alpha=1
beta=0
delta=1
kappa=1
eta=1
lamb=2

In [3]:
def CIR(u,T,y0,kappa,eta, lamb):
    gamma=np.sqrt(kappa**2 - 2*lamb**2*1j*u)
    A=np.exp(kappa**2*eta*T/lamb**2)/(np.cosh(gamma*T/2)+kappa/gamma*np.sinh(gamma*T/2))**(2*kappa*eta/lamb**2)
    B=2*1j*u/(kappa+gamma*np.cosh(gamma*T/2)/np.sinh(gamma*T/2))
    return A*np.exp(B*y0)

In [4]:
def Psi(u, T, r, alpha, beta, delta):
    ''' Funkcja charakterystyczna w modelu CGMY '''
    value = (np.cos(beta/2)/np.cosh((alpha*u-1j*beta)/2))**(2*delta)
    return np.log(value)

In [5]:
def cf(u, T, r, y0, alpha, beta, delta,kappa,eta, lamb):
    return np.exp(u*1j*T*(r-q))*CIR(-1j*Psi(u, T, r, alpha, beta, delta),T, y0, kappa,eta, lamb)/CIR(-1j*Psi(-1j, T, r, alpha, beta, delta),T, y0, kappa,eta, lamb)**(1j*u)

In [6]:
def G(u):
    return np.log(np.exp(u*T*(r-q))*CIR(-1j*Psi(-1j*u, T, r, alpha, beta, delta),T,1, kappa,eta, lamb)/CIR(-1j*Psi(-1j, T, r, alpha,beta,delta),T, 1, kappa,eta, lamb)**(u))

In [7]:
# This class defines puts and calls

N=2**12
L=10
h=1e-3
y0=1

# This class defines puts and calls

class OptionType(enum.Enum):
    CALL = 1.0
    PUT = -1.0
    
def CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta,kappa, eta, lamb,N,L):


    # cf   - Characteristic function is a function, in the book denoted by \varphi
    # CP   - C for call and P for put
    # S0   - Initial stock price
    # r    - Interest rate (constant)
    # T  - Time to maturity
    # K    - List of strikes
    # N    - Number of expansion terms
    # L    - Size of truncation domain (typ.:L=8 or L=10)
        
    # Reshape K to become a column vector

    if K is not np.array:
        K = np.array(K).reshape([len(K),1])
    
    # Assigning i=sqrt(-1)
    
    x0 = np.log(S0 / K)   
    
    # Truncation domain

    c1=(G(h)-G(-h))/(2*h)
    c2=(G(h)-2*G(0)+G(-h))/(h**2)
    c4=(G(3*h)-2*G(2*h)+4*G(0)-G(h)-G(-h)-2*G(-2*h)+G(-3*h))/(4*h**4)

#     c1=grad_g(0., T, theta, beta, sigma, kappa, eta, lamb)
#     c2=grad_g2(0., T, theta, beta, sigma, kappa, eta, lamb)
#     c4=grad_g4(0., T, theta, beta, sigma, kappa, eta, lamb)
    a=c1+x0-L*np.sqrt(c2+np.sqrt(c4))
    b=c1+x0+L*np.sqrt(c2+np.sqrt(c4))
#     Summation from k = 0 to k=N-1

    k = np.linspace(0,N-1,N).reshape([N,1])  
    u = k * np.pi / (b - a);  

    # Determine coefficients for put prices  

    H_k = CallPutCoefficients(CP,a,b,k)   
    mat = np.exp(i * np.outer((x0 - a) , u))
    temp = cf(u, T, r, y0, alpha, beta, delta,kappa,eta, lamb) * H_k 
    temp[0] = 0.5 * temp[0]    
    value = np.exp(-r * T) * K * np.real(mat.dot(temp))     
    return np.exp(-q*T)*S0+ value - K*np.exp(-r*T)

# Determine coefficients for put prices 

def CallPutCoefficients(CP,a,b,k):
    if CP==OptionType.CALL:                  
        c = 0.0
        d = b
        coef = Chi_Psi(a,b,c,d,k)
        Chi_k = coef["chi"]
        Psi_k = coef["psi"]
        if a < b and b < 0.0:
            H_k = np.zeros([len(k),1])
        else:
            H_k = 2.0 / (b - a) * (Chi_k - Psi_k)  
    elif CP==OptionType.PUT:
        c = a
        d = 0.0
        coef = Chi_Psi(a,b,c,d,k)
        Chi_k = coef["chi"]
        Psi_k = coef["psi"]
        H_k  = 2.0 / (b - a) * (- Chi_k + Psi_k)               
    
    return H_k    

def Chi_Psi(a,b,c,d,k):
    psi = np.sin(k * np.pi * (d - a) / (b - a)) - np.sin(k * np.pi * (c - a)/(b - a))
    psi[1:] = psi[1:] * (b - a) / (k[1:] * np.pi)
    psi[0] = d - c
    
    chi = 1.0 / (1.0 + np.power((k * np.pi / (b - a)) , 2.0)) 
    expr1 = np.cos(k * np.pi * (d - a)/(b - a)) * np.exp(d)  - np.cos(k * np.pi 
                  * (c - a) / (b - a)) * np.exp(c)
    expr2 = k * np.pi / (b - a) * np.sin(k * np.pi * 
                        (d - a) / (b - a))   - k * np.pi / (b - a) * np.sin(k 
                        * np.pi * (c - a) / (b - a)) * np.exp(c)
    chi = chi * (expr1 + expr2)
    
    value = {"chi":chi,"psi":psi }
    return value

In [8]:
m=0
def MeixnerSV_error_function(p0):
    
    global m
    alpha, beta, delta, kappa, eta, lamb=p0
    se = []
    for row, option in options.iterrows():
        model_value = CallPutOptionPriceCOSMthd(cf,OptionType.PUT,S0,r,option['T_2'],(option['strike'],),alpha, beta, delta,kappa,eta,lamb,N,L)[0][0]
        se.append((model_value - option['price']) ** 2)
    RMSE = (sum(se) / len(se))**0.5
    if np.isnan(RMSE):
        RMSE=100   
    if m % 1 == 0:
        print('%4d |' % m, np.array(p0), '| %7.3f' % RMSE)
        
    m += 1
    return RMSE
# MeixnerSV_error_function((0.1225, -0.5905, 3.381, 0.5755, 1.5737, 1.952))


In [9]:
def MeixnerSV_calibration_full():
    i=0
    global opt1, opt
    opt1 = spo.brute(MeixnerSV_error_function, ((0.001,1.51, 0.2),(-np.pi,np.pi, 0.5), (0.001,5.2,1),(0.1,1.2,0.2),(0.1,3.3,1), (0.1,3,0.7)), finish=None)
    opt = spo.fmin(MeixnerSV_error_function, opt1, xtol=0.00001, ftol=0.00001, maxiter=15000, maxfun=15000)
    return opt

# %time MeixnerSV_calibration_full()

# Kalibracja dla wielu K

In [10]:
# This class defines puts and calls

N=2**12
L=10
h=1e-3

# This class defines puts and calls

class OptionType(enum.Enum):
    CALL = 1.0
    PUT = -1.0
    
def CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha,beta, delta,kappa, eta, lamb,N,L):


    # cf   - Characteristic function is a function, in the book denoted by \varphi
    # CP   - C for call and P for put
    # S0   - Initial stock price
    # r    - Interest rate (constant)
    # T  - Time to maturity
    # K    - List of strikes
    # N    - Number of expansion terms
    # L    - Size of truncation domain (typ.:L=8 or L=10)
        
    # Reshape K to become a column vector

    if K is not np.array:
        K = np.array(K).reshape([len(K),1])
    
    # Assigning i=sqrt(-1)
    
    x0 = np.log(S0 / K)   

    # kumulanty
    c1=(G(h)-G(-h))/(2*h)
    c2=(G(h)-2*G(0)+G(-h))/(h**2)
    c4=(G(3*h)-2*G(2*h)+4*G(0)-G(h)-G(-h)-2*G(-2*h)+G(-3*h))/(4*h**4)

#     c1=grad_g(0., T, theta, beta, sigma, kappa, eta, lamb)
#     c2=grad_g2(0., T, theta, beta, sigma, kappa, eta, lamb)
#     c4=grad_g4(0., T, theta, beta, sigma, kappa, eta, lamb)
    a=c1-L*np.sqrt(c2+np.sqrt(c4))
    b=c1+L*np.sqrt(c2+np.sqrt(c4))
#     Summation from k = 0 to k=N-1

    k = np.linspace(0,N-1,N).reshape([N,1])  
    u = k * np.pi / (b - a);  

    # Determine coefficients for put prices  

    H_k = CallPutCoefficients(CP,a,b,k)   
    mat = np.exp(i * np.outer((x0 - a) , u))
    temp = cf(u, T, r, y0, alpha, beta, delta, kappa, eta, lamb) * H_k 
    temp[0] = 0.5 * temp[0]    
    value = np.exp(-r * T) * K * np.real(mat.dot(temp))     
    return np.exp(-q*T)*S0+ value - K*np.exp(-r*T)

# Determine coefficients for put prices 

def CallPutCoefficients(CP,a,b,k):
    if CP==OptionType.CALL:                  
        c = 0.0
        d = b
        coef = Chi_Psi(a,b,c,d,k)
        Chi_k = coef["chi"]
        Psi_k = coef["psi"]
        if a < b and b < 0.0:
            H_k = np.zeros([len(k),1])
        else:
            H_k      = 2.0 / (b - a) * (Chi_k - Psi_k)  
    elif CP==OptionType.PUT:
        c = a
        d = 0.0
        coef = Chi_Psi(a,b,c,d,k)
        Chi_k = coef["chi"]
        Psi_k = coef["psi"]
        H_k  = 2.0 / (b - a) * (- Chi_k + Psi_k)               
    
    return H_k    

def Chi_Psi(a,b,c,d,k):
    psi = np.sin(k * np.pi * (d - a) / (b - a)) - np.sin(k * np.pi * (c - a)/(b - a))
    psi[1:] = psi[1:] * (b - a) / (k[1:] * np.pi)
    psi[0] = d - c
    
    chi = 1.0 / (1.0 + np.power((k * np.pi / (b - a)) , 2.0)) 
    expr1 = np.cos(k * np.pi * (d - a)/(b - a)) * np.exp(d)  - np.cos(k * np.pi 
                  * (c - a) / (b - a)) * np.exp(c)
    expr2 = k * np.pi / (b - a) * np.sin(k * np.pi * 
                        (d - a) / (b - a))   - k * np.pi / (b - a) * np.sin(k 
                        * np.pi * (c - a) / (b - a)) * np.exp(c)
    chi = chi * (expr1 + expr2)
    
    value = {"chi":chi,"psi":psi }
    return value

In [11]:
m=0
def MeixnerSV_error_function(p0):
    
    global m
    alpha, beta, delta, kappa,eta,lamb=p0

    se1 = []
    CP=OptionType.PUT
    K = np.array(options1['strike'])
    T=options['T_2'][0]
    model_value=CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta, kappa,eta,lamb,N,L)
    i=0
    for row, option in options1.iterrows():
        se1.append((model_value[i] - option['price']) ** 2)
        i+=1
        
        
    se2 = []
    K = np.array(options2['strike'])
    T=options['T_2'][10]
    model_value=CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta, kappa,eta,lamb,N,L)
    i=0
    for row, option in options2.iterrows():
        se2.append((model_value[i] - option['price']) ** 2)
        i+=1
        
        
    se3 = []    
    K = np.array(options3['strike'])
    T=options['T_2'][18]
    model_value=CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta, kappa,eta,lamb,N,L)
    i=0
    for row, option in options3.iterrows():
        se3.append((model_value[i] - option['price']) ** 2)
        i+=1        
        
        
    se4 = []    
    K = np.array(options4['strike'])
    T=options['T_2'][37]
    model_value=CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta, kappa,eta,lamb,N,L)
    i=0
    for row, option in options4.iterrows():
        se4.append((model_value[i] - option['price']) ** 2)
        i+=1        

    se5 = []    
    K = np.array(options5['strike'])
    T=options['T_2'][48]
    model_value=CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta, kappa,eta,lamb,N,L)
    i=0
    for row, option in options5.iterrows():
        se5.append((model_value[i] - option['price']) ** 2)
        i+=1 
        
    se6 = []    
    K = np.array(options6['strike'])
    T=options['T_2'][58]
    model_value=CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta, kappa,eta,lamb,N,L)
    i=0
    for row, option in options6.iterrows():
        se6.append((model_value[i] - option['price']) ** 2)
        i+=1
        
        
    se7 = []    
    K = np.array(options7['strike'])
    T=options['T_2'][69]
    model_value=CallPutOptionPriceCOSMthd(cf,CP,S0,r,T,K,alpha, beta, delta, kappa,eta,lamb,N,L)
    i=0
    for row, option in options7.iterrows():
        se7.append((model_value[i] - option['price']) ** 2)
        i+=1
        
    RMSE = ((sum(se1)+sum(se2)+sum(se3)+sum(se4)+sum(se5)+sum(se6)+sum(se7)) / (len(se1)+len(se2)+len(se3)+len(se4)+len(se5)+len(se6)+len(se7)))**0.5
    if np.isnan(RMSE):
        RMSE=100
    if m % 1 == 0:
        print('%4d |' % m, np.array(p0), '| %7.3f' % RMSE)
        
    m += 1
    return RMSE

MeixnerSV_error_function((0.1225, -0.5905, 3.381, 0.5755, 1.5737, 1.952))



   0 | [0.1225 -0.5905 3.3810 0.5755 1.5737 1.9520] |   0.493


array([0.4930])

In [12]:
MeixnerSV_calibration_full()

   1 | [0.0010 -3.1416 0.0010 0.1000 0.1000 0.1000] |  48.406
   2 | [0.0010 -3.1416 0.0010 0.1000 0.1000 0.8000] |  48.367
   3 | [0.0010 -3.1416 0.0010 0.1000 0.1000 1.5000] |  48.234
   4 | [0.0010 -3.1416 0.0010 0.1000 0.1000 2.2000] |  48.042
   5 | [0.0010 -3.1416 0.0010 0.1000 0.1000 2.9000] |  47.848
   6 | [0.0010 -3.1416 0.0010 0.1000 1.1000 0.1000] |  48.674
   7 | [0.0010 -3.1416 0.0010 0.1000 1.1000 0.8000] |  48.655
   8 | [0.0010 -3.1416 0.0010 0.1000 1.1000 1.5000] |  48.619
   9 | [0.0010 -3.1416 0.0010 0.1000 1.1000 2.2000] |  48.485
  10 | [0.0010 -3.1416 0.0010 0.1000 1.1000 2.9000] |  48.221
  11 | [0.0010 -3.1416 0.0010 0.1000 2.1000 0.1000] |  48.979
  12 | [0.0010 -3.1416 0.0010 0.1000 2.1000 0.8000] |  48.953
  13 | [0.0010 -3.1416 0.0010 0.1000 2.1000 1.5000] |  48.882
  14 | [0.0010 -3.1416 0.0010 0.1000 2.1000 2.2000] |  48.798
  15 | [0.0010 -3.1416 0.0010 0.1000 2.1000 2.9000] |  48.660
  16 | [0.0010 -3.1416 0.0010 0.1000 3.1000 0.1000] |  49.277
  17 | [

 134 | [0.0010 -3.1416 1.0010 0.1000 2.1000 2.2000] | 443.413
 135 | [0.0010 -3.1416 1.0010 0.1000 2.1000 2.9000] | 436.713
 136 | [0.0010 -3.1416 1.0010 0.1000 3.1000 0.1000] | 446.631
 137 | [0.0010 -3.1416 1.0010 0.1000 3.1000 0.8000] | 446.546
 138 | [0.0010 -3.1416 1.0010 0.1000 3.1000 1.5000] | 446.104
 139 | [0.0010 -3.1416 1.0010 0.1000 3.1000 2.2000] | 443.947
 140 | [0.0010 -3.1416 1.0010 0.1000 3.1000 2.9000] | 438.304
 141 | [0.0010 -3.1416 1.0010 0.3000 0.1000 0.1000] | 446.595
 142 | [0.0010 -3.1416 1.0010 0.3000 0.1000 0.8000] | 446.498
 143 | [0.0010 -3.1416 1.0010 0.3000 0.1000 1.5000] | 445.719
 144 | [0.0010 -3.1416 1.0010 0.3000 0.1000 2.2000] | 441.492
 145 | [0.0010 -3.1416 1.0010 0.3000 0.1000 2.9000] | 431.801
 146 | [0.0010 -3.1416 1.0010 0.3000 1.1000 0.1000] | 446.618
 147 | [0.0010 -3.1416 1.0010 0.3000 1.1000 0.8000] | 446.530
 148 | [0.0010 -3.1416 1.0010 0.3000 1.1000 1.5000] | 446.076
 149 | [0.0010 -3.1416 1.0010 0.3000 1.1000 2.2000] | 443.919
 150 | [

<ipython-input-3-847f22996f3b>:3: RuntimeWarning:

overflow encountered in power

<ipython-input-3-847f22996f3b>:3: RuntimeWarning:

invalid value encountered in true_divide

<ipython-input-3-847f22996f3b>:3: RuntimeWarning:

overflow encountered in cdouble_scalars

<ipython-input-5-ba4f03a56aa4>:2: RuntimeWarning:

invalid value encountered in power

<ipython-input-5-ba4f03a56aa4>:2: RuntimeWarning:

invalid value encountered in true_divide



 237 | [0.0010 -3.1416 1.0010 1.1000 3.1000 0.8000] | 446.699
 238 | [0.0010 -3.1416 1.0010 1.1000 3.1000 1.5000] | 446.537
 239 | [0.0010 -3.1416 1.0010 1.1000 3.1000 2.2000] | 446.123
 240 | [0.0010 -3.1416 1.0010 1.1000 3.1000 2.9000] | 445.235
 241 | [0.0010 -3.1416 2.0010 0.1000 0.1000 0.1000] | 446.954
 242 | [0.0010 -3.1416 2.0010 0.1000 0.1000 0.8000] | 446.951
 243 | [0.0010 -3.1416 2.0010 0.1000 0.1000 1.5000] | 446.907
 244 | [0.0010 -3.1416 2.0010 0.1000 0.1000 2.2000] | 446.301
 245 | [0.0010 -3.1416 2.0010 0.1000 0.1000 2.9000] | 443.846
 246 | [0.0010 -3.1416 2.0010 0.1000 1.1000 0.1000] | 446.954
 247 | [0.0010 -3.1416 2.0010 0.1000 1.1000 0.8000] | 446.951
 248 | [0.0010 -3.1416 2.0010 0.1000 1.1000 1.5000] | 446.919
 249 | [0.0010 -3.1416 2.0010 0.1000 1.1000 2.2000] | 446.505
 250 | [0.0010 -3.1416 2.0010 0.1000 1.1000 2.9000] | 444.696
 251 | [0.0010 -3.1416 2.0010 0.1000 2.1000 0.1000] | 446.954
 252 | [0.0010 -3.1416 2.0010 0.1000 2.1000 0.8000] | 446.951
 253 | [

 371 | [0.0010 -3.1416 3.0010 0.1000 2.1000 0.1000] | 446.957
 372 | [0.0010 -3.1416 3.0010 0.1000 2.1000 0.8000] | 446.957
 373 | [0.0010 -3.1416 3.0010 0.1000 2.1000 1.5000] | 446.954
 374 | [0.0010 -3.1416 3.0010 0.1000 2.1000 2.2000] | 446.894
 375 | [0.0010 -3.1416 3.0010 0.1000 2.1000 2.9000] | 446.461
 376 | [0.0010 -3.1416 3.0010 0.1000 3.1000 0.1000] | 446.957
 377 | [0.0010 -3.1416 3.0010 0.1000 3.1000 0.8000] | 446.957
 378 | [0.0010 -3.1416 3.0010 0.1000 3.1000 1.5000] | 446.955
 379 | [0.0010 -3.1416 3.0010 0.1000 3.1000 2.2000] | 446.908
 380 | [0.0010 -3.1416 3.0010 0.1000 3.1000 2.9000] | 446.572
 381 | [0.0010 -3.1416 3.0010 0.3000 0.1000 0.1000] | 446.957
 382 | [0.0010 -3.1416 3.0010 0.3000 0.1000 0.8000] | 446.956
 383 | [0.0010 -3.1416 3.0010 0.3000 0.1000 1.5000] | 446.952
 384 | [0.0010 -3.1416 3.0010 0.3000 0.1000 2.2000] | 446.824
 385 | [0.0010 -3.1416 3.0010 0.3000 0.1000 2.9000] | 446.015
 386 | [0.0010 -3.1416 3.0010 0.3000 1.1000 0.1000] | 446.957
 387 | [

...

76237 | [0.1243 -0.6004 3.2856 0.5700 1.5705 1.9361] |   0.493
76238 | [0.1242 -0.6004 3.2862 0.5701 1.5703 1.9360] |   0.493
76239 | [0.1242 -0.6004 3.2862 0.5701 1.5703 1.9359] |   0.493
76240 | [0.1242 -0.6004 3.2859 0.5701 1.5704 1.9361] |   0.493
76241 | [0.1242 -0.6004 3.2857 0.5700 1.5705 1.9361] |   0.493
76242 | [0.1242 -0.6004 3.2868 0.5703 1.5702 1.9361] |   0.493
76243 | [0.1242 -0.6004 3.2862 0.5701 1.5702 1.9359] |   0.493
76244 | [0.1242 -0.6004 3.2869 0.5703 1.5701 1.9361] |   0.493
76245 | [0.1242 -0.6003 3.2867 0.5703 1.5703 1.9363] |   0.493
76246 | [0.1242 -0.6004 3.2866 0.5702 1.5703 1.9361] |   0.493
76247 | [0.1242 -0.6004 3.2866 0.5702 1.5702 1.9361] |   0.493
76248 | [0.1242 -0.6004 3.2864 0.5701 1.5704 1.9361] |   0.493
76249 | [0.1242 -0.6004 3.2861 0.5700 1.5703 1.9358] |   0.493
76250 | [0.1242 -0.6004 3.2866 0.5702 1.5703 1.9361] |   0.493
76251 | [0.1242 -0.6003 3.2869 0.5703 1.5702 1.9362] |   0.493
76252 | [0.1242 -0.6004 3.2860 0.5700 1.5704 1.9360] | 

76369 | [0.1234 -0.5953 3.3317 0.5702 1.5744 1.9422] |   0.493
76370 | [0.1233 -0.5945 3.3364 0.5698 1.5759 1.9433] |   0.493
76371 | [0.1230 -0.5927 3.3529 0.5702 1.5774 1.9457] |   0.493
76372 | [0.1233 -0.5936 3.3414 0.5679 1.5780 1.9429] |   0.493
76373 | [0.1231 -0.5938 3.3470 0.5699 1.5755 1.9435] |   0.493
76374 | [0.1231 -0.5940 3.3505 0.5705 1.5738 1.9430] |   0.493
76375 | [0.1231 -0.5937 3.3475 0.5712 1.5756 1.9455] |   0.493
76376 | [0.1232 -0.5936 3.3429 0.5688 1.5774 1.9435] |   0.493
76377 | [0.1230 -0.5924 3.3547 0.5691 1.5782 1.9451] |   0.493
76378 | [0.1230 -0.5924 3.3549 0.5697 1.5776 1.9460] |   0.493
76379 | [0.1232 -0.5936 3.3435 0.5685 1.5772 1.9435] |   0.493
76380 | [0.1231 -0.5929 3.3501 0.5684 1.5779 1.9438] |   0.493
76381 | [0.1230 -0.5930 3.3536 0.5693 1.5764 1.9440] |   0.493
76382 | [0.1232 -0.5940 3.3427 0.5691 1.5758 1.9430] |   0.493
76383 | [0.1233 -0.5948 3.3367 0.5692 1.5746 1.9419] |   0.493
76384 | [0.1230 -0.5930 3.3543 0.5696 1.5761 1.9444] | 

76502 | [0.1225 -0.5907 3.3807 0.5749 1.5733 1.9511] |   0.493
76503 | [0.1226 -0.5907 3.3792 0.5743 1.5738 1.9505] |   0.493
76504 | [0.1226 -0.5908 3.3782 0.5741 1.5741 1.9505] |   0.493
76505 | [0.1225 -0.5906 3.3795 0.5743 1.5742 1.9508] |   0.493
76506 | [0.1225 -0.5906 3.3814 0.5747 1.5736 1.9509] |   0.493
76507 | [0.1225 -0.5904 3.3839 0.5750 1.5734 1.9513] |   0.493
76508 | [0.1226 -0.5909 3.3789 0.5746 1.5731 1.9502] |   0.493
76509 | [0.1226 -0.5908 3.3791 0.5745 1.5734 1.9504] |   0.493
76510 | [0.1225 -0.5909 3.3792 0.5746 1.5734 1.9504] |   0.493
76511 | [0.1225 -0.5908 3.3797 0.5743 1.5736 1.9504] |   0.493
76512 | [0.1225 -0.5908 3.3808 0.5749 1.5728 1.9505] |   0.493
76513 | [0.1226 -0.5908 3.3789 0.5743 1.5738 1.9505] |   0.493
76514 | [0.1226 -0.5908 3.3790 0.5747 1.5734 1.9505] |   0.493
76515 | [0.1225 -0.5908 3.3795 0.5744 1.5736 1.9505] |   0.493
76516 | [0.1225 -0.5906 3.3806 0.5748 1.5734 1.9510] |   0.493
76517 | [0.1225 -0.5906 3.3804 0.5745 1.5737 1.9509] | 

76634 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76635 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76636 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76637 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76638 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76639 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76640 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76641 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76642 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76643 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76644 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76645 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76646 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76647 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76648 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] |   0.493
76649 | [0.1225 -0.5905 3.3822 0.5748 1.5735 1.9510] | 

array([0.1225, -0.5905, 3.3822, 0.5748, 1.5735, 1.9510])